In [1]:
from pyecharts.globals import CurrentConfig, OnlineHostType

# OnlineHostType.NOTEBOOK_HOST 默认值为 http://localhost:8888/nbextensions/assets/
CurrentConfig.ONLINE_HOST = OnlineHostType.NOTEBOOK_HOST
import pandas as pd
import numpy as np
import time
import talib
from datetime import datetime, timedelta
from scipy.signal import argrelextrema
from statsmodels.nonparametric.kernel_regression import KernelReg
from binance.client import Client
from IPython.display import display, clear_output
from pyecharts.charts import Kline, Line, Grid, Scatter
from pyecharts import options as opts
import progressbar

In [2]:
client=Client(api_key = pw.key 
              ,api_secret = pw.secret)

In [3]:
def sar(acceleration, maximum):
    low = []
    high = []
    for i in range(len(crypto_visualize.final)):
        low.append(crypto_visualize.final[i][2])
        high.append(crypto_visualize.final[i][3])
    data = {"high":high,"low":low}
    df = pd.DataFrame(data)
    tab_sar = talib.SAR(df['high'],df['low'],acceleration,maximum)
    
    list_sar = tab_sar.tolist()
    return list_sar

In [4]:
def kdj(kdj_length, k, d, ret):
    RSV = []
    kvalue = []
    dvalue = []
    jvalue = []
    c = 1
    
    while c < k:
        kvalue.append(50)
        dvalue.append(50)
        RSV.append(50)
        jvalue.append(3*kvalue[-1]-2*dvalue[-1])
        c = c + 1
    
    for j in range(k-1, len(crypto_visualize.final_date)):
        high = []
        low = []
        k_period = crypto_visualize.final[j-k+1:j+1]
        for i in range(len(k_period)):
            low.append(k_period[i][2])
            high.append(k_period[i][3])
        lowest = min(low)
        highest = max(high)
        if highest - lowest == 0:
            RSV.append(50)
        else:
            RSV.append(100*(crypto_visualize.final[j][1] - lowest)/(highest-lowest))
        kvalue.append(2/3*kvalue[j-1]+RSV[j]/3)
        dvalue.append(2/3*dvalue[j-1]+kvalue[j]/3)
        jvalue.append(3*kvalue[j]-2*dvalue[j]) 
    
    if ret == 'k':
        return kvalue
    
    elif ret == 'd':
        return dvalue
    
    elif ret == 'j':
        return jvalue

In [5]:
def boll(boll_length, boll_multipler, boll_ret):
    result: List[Union[float, str]] = []
    upper: List[Union[float, str]] = []
    lower: List[Union[float, str]] = []
    

    for i in range(len(crypto_visualize.final_date)):
        if i < boll_length:
            result.append("-")
            upper.append("-")
            lower.append("-")
            continue
        sum_total = 0.0
        close = []

        for j in range(boll_length):
            close.append(float(crypto_visualize.final[i - j][1]))
            sum_total += float(crypto_visualize.final[i - j][1])
        result.append(abs(float("%.6f" % (sum_total / boll_length))))
        std = np.std(close)
        upper.append(result[-1] + std*2)
        lower.append(result[-1] - std*2)
        
    if boll_ret == "sma":    
        return result
    elif boll_ret == "upper":
        return upper
    elif boll_ret == "lower":
        return lower

In [6]:
def crypto_visualize(ticker,k ,d, kdj_length, boll_length, boll_multipler, acceleration, maximum,
                     interval = Client.KLINE_INTERVAL_1MINUTE,start_at=None,end_at=None):
    
    final = []
    final_date = []
     
    n = 1
    today = datetime.today()
    today = today.strftime("%Y/%m/%d, %H:%M")
    today_new = datetime.strptime(today, "%Y/%m/%d, %H:%M")
    dict_setup = {"time":[],"open":[], "high":[], "low":[], "close":[]}
    minute_data = []
    oneyear = today_new - timedelta(days=365)
    oneyear_mili = round(oneyear.timestamp()*1000)
    oneyear = oneyear.strftime("%Y/%m/%d, %H:%M")
        
    year_data = client.futures_klines(symbol = ticker, interval = interval,startTime=oneyear_mili, limit=1440)
    yearcheck = datetime.fromtimestamp(int(year_data[0][0]/1000))
    readable_yearcheck = yearcheck.strftime("%Y/%m/%d, %H:%M")
    
    if start_at is None:
        if oneyear >= readable_yearcheck:
            while n <= 364:
                year_ago_fixed = today_new - timedelta(days=365-n)
                year_ago_mili = round(year_ago_fixed.timestamp()*1000)
                klines = client.futures_klines(symbol = ticker, interval = interval, startTime=year_ago_mili, limit=1440)
                minute_data.append(klines)
                n = n + 1
                time.sleep(0.07)
        else:
            readable_yearcheck_datetime = datetime.strptime(readable_yearcheck,"%Y/%m/%d, %H:%M")
            time_diff = today_new - readable_yearcheck_datetime
            time_diff = time_diff.days
            while n <= time_diff-1:
                time_ago_fixed = today_new - timedelta(days=time_diff-n)
                time_ago_mili = round(time_ago_fixed.timestamp()*1000)
                klines = client.futures_klines(symbol = ticker, interval = interval, startTime=time_ago_mili, limit=1440)
                minute_data.append(klines)
                n = n + 1
                time.sleep(0.07)
                
    elif start_at is not None:
        start_at_datetime = datetime.strptime(start_at, "%Y/%m/%d, %H:%M")
        end_at_datetime = datetime.strptime(end_at, "%Y/%m/%d, %H:%M")
        time_diff = end_at_datetime - start_at_datetime
        time_diff = time_diff.days
        
        while n <= time_diff-1:
            start_at_fixed = end_at_datetime - timedelta(days=time_diff-n)
            start_at_mili = round(start_at_fixed.timestamp()*1000)
            klines = client.futures_klines(symbol = ticker, contractType = "PERPETUAL",
                                            interval = Client.KLINE_INTERVAL_1MINUTE,startTime=start_at_mili, limit=1440)
            minute_data.append(klines)
            n = n + 1
            print("One minute kline data from "+start_at+" found! Extracted",n,"days of data!")
            clear_output(wait=True)
            time.sleep(0.07)
    
    for m in range(len(minute_data)):
        for l in range(len(minute_data[m])):
            raw_date = minute_data[m][l][0]
            close = float(minute_data[m][l][4])
            op = float(minute_data[m][l][1])
            high = float(minute_data[m][l][2])
            low = float(minute_data[m][l][3])
            date = datetime.fromtimestamp(int(raw_date/1000))
            readable_date = date.strftime("%Y/%m/%d, %H:%M")
            final_date.append(readable_date)
            final.append([op,close,low,high])
    
    crypto_visualize.final_date = final_date
    crypto_visualize.final = final
    
    kline = (
        Kline()
        .add_xaxis(final_date)
        .add_yaxis(
        "Kline",
        final,
        markpoint_opts=opts.MarkPointOpts(
        data=[
            opts.MarkPointItem(type_="max", value_dim="close", name="Maximum closing price"),
            opts.MarkPointItem(type_="min", value_dim="close", name="Minimum closing price"),
            ]
        ),
        itemstyle_opts=opts.ItemStyleOpts(
        color="#ec0000", color0="#00da3c"
        ),
        ) 
        .set_global_opts(
        xaxis_opts=opts.AxisOpts(is_scale=True),
        yaxis_opts=opts.AxisOpts(
        is_scale=True,
        splitarea_opts=opts.SplitAreaOpts(
        is_show=True, areastyle_opts=opts.AreaStyleOpts(opacity=1)
            )
        ),
        datazoom_opts=[
            opts.DataZoomOpts(
                is_show=False,
                type_="inside",
                xaxis_index=[0,1],
                range_start=80, 
                range_end=100,
            ),
            opts.DataZoomOpts(
                is_show=True,
                xaxis_index=[0,1],
                type_="slider",
                pos_bottom="-1%", 
                range_start=80, 
                range_end=100,
            ),
        ],
        title_opts=opts.TitleOpts(title=ticker),
            )
        )
        
    boll_line = (
        Line()
        .add_xaxis(xaxis_data=final_date)
        .add_yaxis(
            series_name = "Mid",
            y_axis = boll(boll_length, boll_multipler, "sma"),
            is_smooth=True,
            linestyle_opts=opts.LineStyleOpts(opacity=1.5),
            label_opts=opts.LabelOpts(is_show=False),

        )
        .add_yaxis(
            series_name = "Upper",
            y_axis = boll(boll_length, boll_multipler, "upper"),
            is_smooth=True,
            linestyle_opts=opts.LineStyleOpts(opacity=1.5),
            label_opts=opts.LabelOpts(is_show=False),

        )
        .add_yaxis(
            series_name = "Lower",
            y_axis = boll(boll_length, boll_multipler, "lower"),
            is_smooth=True,
            linestyle_opts=opts.LineStyleOpts(opacity=1.5),
            label_opts=opts.LabelOpts(is_show=False),

        )
        .set_global_opts(
            xaxis_opts=opts.AxisOpts(
                type_ ='Category',
                axislabel_opts=opts.LabelOpts(is_show=False),
            ),
        )
    )
    
    sar_scatter = (
        Scatter()
        .add_xaxis(
            final_date,
        )
        .add_yaxis(
            series_name = "SAR",
            y_axis=sar(acceleration, maximum),
            symbol_size=5.5,
            itemstyle_opts=opts.ItemStyleOpts(
            color="purple",
            ),
            label_opts=opts.LabelOpts(is_show=False),
        )
        .set_global_opts(
            xaxis_opts=opts.AxisOpts(
                type_='Category',
                axislabel_opts=opts.LabelOpts(is_show=False),
            ),
        )
    )
    
    overlap_kline_line = kline.overlap(boll_line)
    overlap_all = overlap_kline_line.overlap(sar_scatter)
        
    kdj_line = (
        Line()
        .add_xaxis(
            final_date,
        )
        .add_yaxis(
            series_name='K',
            y_axis = kdj(kdj_length,k,d,'k'),
            is_smooth=True,
            linestyle_opts=opts.LineStyleOpts(opacity=1.5),
            label_opts=opts.LabelOpts(is_show=False),
            xaxis_index=1,
            yaxis_index=1,
            itemstyle_opts=opts.ItemStyleOpts(
            color="red",
            ),

        )
        .add_yaxis(
            series_name='D',
            y_axis=kdj(kdj_length,k,d,'d'),
            is_smooth=True,
            linestyle_opts=opts.LineStyleOpts(opacity=1.5),
            label_opts=opts.LabelOpts(is_show=False),
            xaxis_index=1,
            yaxis_index=1,
            itemstyle_opts=opts.ItemStyleOpts(
            color="blue",
        ),

        )
        .add_yaxis(
            series_name='J',
            y_axis=kdj(kdj_length,k,d,'j'),
            is_smooth=True,
            linestyle_opts=opts.LineStyleOpts(opacity=1.5),
            label_opts=opts.LabelOpts(is_show=False),
            xaxis_index=1,
            yaxis_index=1,
            itemstyle_opts=opts.ItemStyleOpts(
            color="purple",
        ),

        )
        .set_global_opts(
            xaxis_opts=opts.AxisOpts(
            grid_index=1,
            ),
            yaxis_opts=opts.AxisOpts(
            grid_index=1,
            ),
            legend_opts=opts.LegendOpts(is_show=False),
        )
    )
        
    grid_chart = Grid(init_opts=opts.InitOpts(width="900px", height="700px"))
        
    grid_chart.add(
        overlap_all,
        grid_opts=opts.GridOpts(pos_left="5%", pos_right="1%",pos_bottom="40%", height="50%"),
    )
    grid_chart.add(
        kdj_line,
        grid_opts=opts.GridOpts(
            pos_left="5%", pos_right='1%', pos_top="70%", height="130"),
    )
    
    return grid_chart.render_notebook()

In [9]:
crypto_visualize(ticker="DOGEUSDT", start_at = '2021/05/06, 20:00', end_at = '2021/05/09, 20:00', k=9, d=3, kdj_length=3,
            boll_length = 20, boll_multipler = 2, acceleration = 0.02, maximum=0.2)